In [16]:
from map_figure import mapFigure, convert_crs

import plotly.graph_objects as go
import plotly.express as px
import pandas as pd

In [17]:
russia_map = mapFigure()
russia_map.show()

In [18]:
import pandas as pd
import plotly.express as px

regions = pd.read_parquet("data/russia_regions.parquet")
fo_list = list(regions['federal_district'].unique())
colors = px.colors.qualitative.Pastel1

for i, r in regions.iterrows():
    popul_text = f"Население: <b>{r.population:_} </b>".replace('_', ' ')
    text = f'<b>{r.region}</b><br>{r.federal_district} ФО<br>{popul_text}'
    russia_map.update_traces(selector=dict(name=r.region),
        text=text,
        fillcolor=colors[fo_list.index(r.federal_district)])
russia_map.show()

In [19]:
df_m = pd.read_csv('data/protest_fin.csv')
df_m

Event ID  Event Date            Event Text  Story ID        City  \
0     37534934  2023-01-03  Demonstrate or rally  56612931      Samara   
1     37571701  2022-10-18  Demonstrate or rally  56698583         NaN   
2     37622281  2023-02-02  Demonstrate or rally  56805909   Volgograd   
3     37634619  2023-02-08  Demonstrate or rally  56833395  Khabarovsk   
4     37640304  2023-02-10  Demonstrate or rally  56844966  Khabarovsk   
...        ...         ...                   ...       ...         ...   
3424  37465941  2022-11-05  Demonstrate or rally  56452595   Tatarstan   
3425  37465942  2022-11-05  Demonstrate or rally  56452595   Tatarstan   
3426  37515897  2022-12-26  Demonstrate or rally  56565804      Berkut   
3427  37534529  2023-01-03  Demonstrate or rally  56606014      Samara   
3428  37534530  2023-01-03  Demonstrate or rally  56606014   Tol'yatti   

                District                Province  Latitude  Longitude  Year  \
0                    NaN      Samarskaya Oblast'   53.2001    50.1500  2023   
1                    NaN           North Ossetia   43.0000    44.2500  2022   
2                    NaN  Volgogradskaya Oblast'   48.7194    44.5018  2023   
3     Khabarovskiy Rayon       Khabarovskiy Kray   48.4827   135.0840  2023   
4     Khabarovskiy Rayon       Khabarovskiy Kray   48.4827   135.0840  2023   
...                  ...                     ...       ...        ...   ...   
3424                 NaN               Tatarstan   56.1292    53.3703  2022   
3425                 NaN               Tatarstan   56.1292    53.3703  2022   
3426                 NaN   Orenburgskaya Oblast'   51.2921    57.7054  2022   
3427                 NaN      Samarskaya Oblast'   53.2001    50.1500  2023   
3428                 NaN      Samarskaya Oblast'   53.5303    49.3461  2023   

                                           municipality  
0              Чернореченская улица, 67, Самара, 443013  
1     Государственный природный заказник Цейский, Ал...  
2             Черноморская улица, 42, Волгоград, 400012  
3                                парк Динамо, Хабаровск  
4                                парк Динамо, Хабаровск  
...                                                 ...  
3424  Кадыбашское сельское поселение, Агрызский райо...  
3425  Кадыбашское сельское поселение, Агрызский райо...  
3426  Государственный природный заказник областного ...  
3427           Чернореченская улица, 67, Самара, 443013  
3428           квартал 14А, Тольятти, Самарская область  

[3429 rows x 11 columns]

In [20]:
df = pd.read_parquet("data/russia_cities_population.parquet")
df

city                   region federal_district  population  \
0         Абаза       Республика Хакасия        Сибирский       12272   
1        Абакан       Республика Хакасия        Сибирский      184769   
2      Абдулино     Оренбургская область      Приволжский       17274   
3        Абинск       Краснодарский край            Южный       39511   
4       Агидель  Республика Башкортостан      Приволжский       14219   
...         ...                      ...              ...         ...   
1128  Ярославль      Ярославская область      Центральный      577279   
1129     Ярцево       Смоленская область      Центральный       41452   
1130  Ясногорск         Тульская область      Центральный       15269   
1131      Ясный     Оренбургская область      Приволжский       15471   
1132     Яхрома       Московская область      Центральный       14011   

             lat         lon  
0          52.65    90.08333  
1       53.71667    91.41667  
2       53.68333       53.65  
3       44.86667    38.16667  
4           55.9    53.93333  
...          ...         ...  
1128    57.61667       39.85  
1129    55.06667    32.68333  
1130  54.4793833  37.6933556  
1131    51.03333    59.86667  
1132    56.28333    37.48333  

[1133 rows x 6 columns]

In [21]:
df['x'], df['y'] = convert_crs(df_m.Longitude, df_m.Latitude)
# палитра цветов для точек
cities_palette = {fd: px.colors.qualitative.Dark2_r[i] for i, fd in enumerate(df.federal_district.unique())}

# добавление точек на фигуру
russia_map.add_trace(go.Scatter(
    x=df.x, y=df.y, name='города',
    # text="<b>"+df.city+"</b><br>Население <b>"+df.population.astype('str')+"</b>",
    hoverinfo="text", showlegend=False, mode='markers',
    # marker_size=df.population/1e4, marker_sizemode='area', marker_sizemin=3,
    marker_color=df.federal_district.map(cities_palette)
))

russia_map.show()

In [31]:
from ipyleaflet import Map, Circle, LayerGroup, basemaps
def show_circles_on_map(data, latitude_column, longitude_column, color):
    """
    The function draws map with circles on it.
    The center of the map is the mean of coordinates passed in data.

    data: DataFrame that contains columns latitude_column and longitude_column
    latitude_column: string, the name of column for latitude coordinates
    longitude_column: string, the name of column for longitude coordinates
    color: string, the color of circles to be drawn
    """

    center = (data[latitude_column].mean(), data[longitude_column].mean())
    result_map = Map(center=center, zoom=10, basemap=basemaps.Esri.NatGeoWorldMap)

    circles = []
    for _, row in data.iterrows():
        circles.append(Circle(
            location=(row[latitude_column], row[longitude_column]),
            fill_color=color,
            fill_opacity=0.2,
            radius=30000,                                               # РАДИУС КРУЖОЧКОВ
            stroke=False
        ))
    circles_layer = LayerGroup(layers=circles)
    result_map.add_layer(circles_layer)

    return result_map

show_circles_on_map(df_m, 'Latitude', 'Longitude', "blue")


Map(center=[51.71602764654418, 57.046501428988044], controls=(ZoomControl(options=['position', 'zoom_in_text',…